In [53]:
import mat4py
import numpy as np
import pandas as pd
import lanelet2
from pyproj import Proj, transform

In [54]:
# read matlab file
data = mat4py.loadmat('/home/matyko/Documents/Ll2_mapping/ll2_raw.mat')

In [55]:
def diff_to (x1, y1, x2, y2):
    return np.sqrt((x2 - x1)**2 + (y2 - y1)**2)

In [56]:
lanes = []

for i in range(len(data["lanelets"])):
    path = np.array(data["lanelets"][i]["centerLine"])
    leftLane = np.array([])
    rightLane = np.array([])
    end_coord = path[-1]
    left_index = 0
    right_index = 0
    for line in data["lanelets"][i]["leftLine"]:
        if diff_to(line[0],line[1],end_coord[0],end_coord[1]) < 2.0:
            break
        left_index += 1
    for line in data["lanelets"][i]["rightLine"]:
        if diff_to(line[0],line[1],end_coord[0],end_coord[1]) < 2.0:
            break
        right_index += 1
    leftLane = np.array(data["lanelets"][i]["leftLine"][:left_index])
    rightLane = np.array(data["lanelets"][i]["rightLine"][:right_index])

    lanes.append([path,leftLane,rightLane])

In [57]:
import numpy as np
from pyproj import Proj, Transformer

# Define the UTM and WGS84 projections
utm = Proj(proj='utm', zone=33, ellps='WGS84')  # Adjust the zone as needed
wgs84 = Proj(proj='latlong', datum='WGS84')  # WGS84 coordinate system

# Create a transformer object
transformer = Transformer.from_proj(utm, wgs84)

def convert_to_wgs84(utm_coords):
    return np.array([transformer.transform(x, y) for x, y in utm_coords])

lanes = []

for i in range(len(data["lanelets"])):
    path = np.array(data["lanelets"][i]["centerLine"])
    leftLane = np.array([])
    rightLane = np.array([])
    end_coord = path[-1]
    left_index = 0
    right_index = 0
    for line in data["lanelets"][i]["leftLine"]:
        if diff_to(line[0], line[1], end_coord[0], end_coord[1]) < 2.0:
            break
        left_index += 1
    for line in data["lanelets"][i]["rightLine"]:
        if diff_to(line[0], line[1], end_coord[0], end_coord[1]) < 2.0:
            break
        right_index += 1
    leftLane = np.array(data["lanelets"][i]["leftLine"][:left_index])
    rightLane = np.array(data["lanelets"][i]["rightLine"][:right_index])

    # Convert UTM coordinates to WGS84
    path_wgs84 = convert_to_wgs84(path)
    leftLane_wgs84 = convert_to_wgs84(leftLane)
    rightLane_wgs84 = convert_to_wgs84(rightLane)

    lanes.append([path, leftLane, rightLane])

In [58]:
lanes[0][0]

array([[ 640204.1950422 , 5194103.25388874],
       [ 640204.18420814, 5194103.35330111],
       [ 640204.17337408, 5194103.45271348],
       ...,
       [ 640344.47348971, 5195370.11513857],
       [ 640344.61781127, 5195370.14043695],
       [ 640344.76222665, 5195370.16567417]])

In [59]:
#plot lane1 using plotly
import plotly.graph_objects as go

fig = go.Figure()
# plot with the same scale for x and y
fig.update_xaxes(scaleanchor = "y", scaleratio = 1)

for lane in lanes:
    fig.add_trace(go.Scatter(x = lane[0][:,0], y = lane[0][:,1], mode='lines', name='centerLine'))
    fig.add_trace(go.Scatter(x = lane[1][:,0], y = lane[1][:,1], mode='lines', name='leftLane'))
    fig.add_trace(go.Scatter(x = lane[2][:,0], y = lane[2][:,1], mode='lines', name='rightLane'))

fig.show()




In [70]:
import lanelet2
import lanelet2.core as l2_core
import lanelet2.io as l2_io
import lanelet2.projection as l2_proj
import lanelet2.projection
import lanelet2.traffic_rules as l2_rules
import os

left_points = []
right_points = []
center_points = []

# Create a Lanelet map and add the lanelet
lanelet_map = l2_core.LaneletMap()

for lane in lanes:

    left_points.clear()
    right_points.clear()
    center_points.clear()

    for i, points in enumerate(lane[1]):
        if i % 10 == 0:
            left_points.append(l2_core.Point3d(l2_core.getId(), points[0] - 500000, points[1] , 0))

    for i, points in enumerate(lane[2]):
        if i % 10 == 0:
            right_points.append(l2_core.Point3d(l2_core.getId(), points[0] - 500000, points[1] , 0))

    for i, points in enumerate(lane[0]):
        if i % 10 == 0:
            center_points.append(l2_core.Point3d(l2_core.getId(), points[0] - 500000, points[1] , 0))


    # delete the last 10 points from the left and right lane
    left_points = left_points[:-10]
    right_points = right_points[:-10]
    center_points = center_points[:-10]

    # Create LineStrings (borders of the lanelet)
    left_ls = l2_core.LineString3d(l2_core.getId(), left_points)
    right_ls = l2_core.LineString3d(l2_core.getId(), right_points)
    center_ls = l2_core.LineString3d(l2_core.getId(), center_points)


    # Create a lanelet from the left and right boundaries
    lanelet = l2_core.Lanelet(l2_core.getId(), left_ls, right_ls)

    # Set some attributes for the laneletb
    lanelet.attributes["subtype"] = "road"
    lanelet.attributes["one_way"] = "yes"

    lanelet_map.add(lanelet)

    # Add the linestrings to the map
    lanelet_map.add(left_ls)
    lanelet_map.add(right_ls)

projection = lanelet2.projection.UtmProjector(lanelet2.io.Origin(0,15.0))

# Write the map to an OSM file
map_file = "lightweight_lanelet.osm"
l2_io.write(map_file, lanelet_map,projection)
print(f"Lanelet2 map has been saved to {map_file}")


Lanelet2 map has been saved to lightweight_lanelet.osm


In [61]:
46.88609333253 + 0.00042401968

46.88651735221

In [62]:
# lat 
46.88567158 - 0.00042401968

46.88524756032

In [63]:
#lon 
16.84027004 - 0.00015127849

16.84011876151

In [64]:
# UTM x
640219.929 - 640204.195

15.734000000054948

In [65]:
# UTM y
5194150.514 - 5194103.253

47.26100000087172

In [66]:
640219.929 - 15.734000000054948

640204.195

In [67]:
5194150.514 - 47.26100000087172

5194103.253